# MNIST with convolutional networks

## Reading the data

In [ ]:
import numpy as np,tensorflow as tf

import matplotlib as mpl
import matplotlib.pyplot as plt
import seaborn as sns
sns.set_style("whitegrid")
sns.set_palette("colorblind")
palette = sns.color_palette()
figsize = (10,10)
legend_fontsize = 16

In [ ]:
from tensorflow.examples.tutorials.mnist import input_data
mnist = input_data.read_data_sets("MNIST_data/", one_hot=True)

## Convolutions in TensorFlow

In [ ]:
x = tf.placeholder(tf.float32, [None, 784]) 
y = tf.placeholder(tf.float32, [None, 10])
keep_probability = tf.placeholder(tf.float32)

x_image = tf.reshape(x, [-1,28,28,1])

W_conv_0 = tf.Variable(tf.truncated_normal([5, 5, 1, 32], stddev=0.1))
b_conv_0 = tf.Variable(tf.constant(0.1, shape=[32]))

conv_0 = tf.nn.conv2d(x_image, W_conv_0, strides=[1, 1, 1, 1], padding='SAME') + b_conv_0

h_conv_0 = tf.nn.relu(conv_0)
h_pool_0 = tf.nn.max_pool(h_conv_0, ksize=[1, 2, 2, 1], strides=[1, 2, 2, 1], padding='SAME')
h_pool_1_flat = tf.reshape(h_pool_0, [-1, 14*14*32])

W_fc_1 = tf.Variable(tf.truncated_normal([14*14*32, 10], stddev=0.1))
b_fc_1 = tf.Variable(tf.constant(0.1, shape=[10]))

logit_conv = tf.matmul(h_pool_1_flat, W_fc_1) + b_fc_1
y_conv = tf.nn.softmax(logit_conv)

In [ ]:
correct_prediction = tf.equal(tf.argmax(y_conv, 1), tf.argmax(y, 1))
accuracy = tf.reduce_mean(tf.cast(correct_prediction, tf.float32))

l2 = tf.contrib.layers.l2_regularizer(0.1)
cross_entropy = tf.reduce_mean(tf.nn.softmax_cross_entropy_with_logits(logits=logit_conv, labels=y)) + \
                    l2(W_conv_0) #+ l2(W_conv_1)# + l1(W_conv_0) + l1(W_conv_1) + l1(W_conv_2)

train_step = tf.train.AdamOptimizer(0.0001).minimize(cross_entropy)

In [ ]:
sess = tf.Session()
sess.run(tf.global_variables_initializer())

In [ ]:
for i in range(2001):
    batch_xs, batch_ys = mnist.train.next_batch(64)
    sess.run(train_step, feed_dict={x: batch_xs, y: batch_ys, keep_probability: 0.5})
    if i % 50 == 0:
        test_xs, test_ys = mnist.test.next_batch(128)
        acc = sess.run(accuracy, feed_dict={x: test_xs, y: test_ys, keep_probability: 1.})
        print("Accuracy %s: %s" % (i, acc))
    if i > 0 and i % 1000 == 0:
        print("[%d]\ttrain accuracy\ttest accuracy=%.6f" % (i,
#             sess.run(accuracy, feed_dict={x: mnist.train.images, y: mnist.train.labels}),
            sess.run(accuracy, feed_dict={x: mnist.test.images, y: mnist.test.labels})
        ))

## Two-layer convolutional network

In [ ]:
x = tf.placeholder(tf.float32, [None, 784]) 
y = tf.placeholder(tf.float32, [None, 10])
keep_probability = tf.placeholder(tf.float32)

x_image = tf.reshape(x, [-1,28,28,1])

W_conv_0 = tf.Variable(tf.truncated_normal([5, 5, 1, 32], stddev=0.1))
b_conv_0 = tf.Variable(tf.constant(0.1, shape=[32]))

conv_0 = tf.nn.conv2d(x_image, W_conv_0, strides=[1, 1, 1, 1], padding='SAME') + b_conv_0

h_conv_0 = tf.nn.relu(conv_0)
h_pool_0 = tf.nn.max_pool(h_conv_0, ksize=[1, 2, 2, 1], strides=[1, 2, 2, 1], padding='SAME')

W_conv_1 = tf.Variable(tf.truncated_normal([5, 5, 32, 64], stddev=0.1))
b_conv_1 = tf.Variable(tf.constant(0.1, shape=[64]))

conv_1 = tf.nn.conv2d(h_pool_0, W_conv_1, strides=[1, 1, 1, 1], padding='SAME') + b_conv_1

h_conv_1 = tf.nn.relu(conv_1)
h_pool_1 = tf.nn.max_pool(h_conv_1, ksize=[1, 2, 2, 1], strides=[1, 2, 2, 1], padding='SAME')
h_pool_1_flat = tf.reshape(h_pool_1, [-1, 7*7*64])

W_fc_2 = tf.Variable(tf.truncated_normal([7*7*64, 10], stddev=0.1))
b_fc_2 = tf.Variable(tf.constant(0.1, shape=[10]))

logit_conv = tf.matmul(h_pool_1_flat, W_fc_2) + b_fc_2
y_conv = tf.nn.softmax(logit_conv)

In [ ]:
correct_prediction = tf.equal(tf.argmax(y_conv, 1), tf.argmax(y, 1))
accuracy = tf.reduce_mean(tf.cast(correct_prediction, tf.float32))

l2 = tf.contrib.layers.l2_regularizer(0.1)
cross_entropy = tf.reduce_mean(tf.nn.softmax_cross_entropy_with_logits(logits=logit_conv, labels=y))
#+ \
 #                   l2(W_conv_0) #+ l2(W_conv_1)# + l1(W_conv_0) + l1(W_conv_1) + l1(W_conv_2)

train_step = tf.train.AdamOptimizer().minimize(cross_entropy)

In [ ]:
sess = tf.Session()
sess.run(tf.initialize_all_variables())

In [ ]:
for i in range(2001):
    batch_xs, batch_ys = mnist.train.next_batch(64)
    sess.run(train_step, feed_dict={x: batch_xs, y: batch_ys, keep_probability: 0.5})
    if i % 50 == 0:
        test_xs, test_ys = mnist.test.next_batch(128)
        acc = sess.run(accuracy, feed_dict={x: test_xs, y: test_ys, keep_probability: 1.})
        print("Accuracy %s: %s" % (i, acc))
    if i > 0 and i % 1000 == 0:
        print("[%d]\ttest accuracy=%.6f" % (i,
#             sess.run(accuracy, feed_dict={x: mnist.train.images, y: mnist.train.labels}),
            sess.run(accuracy, feed_dict={x: mnist.test.images, y: mnist.test.labels})
        ))